# PyAnsys Geometry 101: Plotter
This example provides an overview of PyAnsys Geometry's plotting capabilities, focusing on
its plotter features. After reviewing the fundamental concepts of sketching
and modeling in PyAnsys Geometry, it shows how to leverage these key plotting capabilities:

- **Multi-object plotting**: You can conveniently plot a list of elements, including objects
  created in both PyAnsys Geometry and PyVista libraries.
- **Interactive object selection**: You can interactively select PyAnsys Geometry objects within the
  scene. This enables efficient manipulation of these objects in subsequent scripting.

## Perform required imports

Perform the required imports.

In [1]:
from pint import Quantity
import pyvista as pv

from ansys.geometry.core.math import Point2D
from ansys.geometry.core.misc import UNITS
from ansys.geometry.core.plotting import GeometryPlotter
from ansys.geometry.core.sketch import Sketch

## Launch modeling service

Launch a modeling service session.

In [2]:
from ansys.geometry.core import launch_modeler

# Start a modeler session
modeler = launch_modeler()
print(modeler)

Ansys Geometry Modeler (0x7fd6e68b3230)

Ansys Geometry Modeler Client (0x7fd6e68b3380)
  Target:     localhost:700
  Connection: Healthy
  Backend info:
    Version:            26.1.0
    Backend type:       CORE_LINUX
    Backend number:     20250925.6
    API server number:  1306
    CADIntegration:     1.1.0.83


You can also launch your own services and connect to them. For information on
connecting to an existing service, see the
[Modeler API](https://geometry.docs.pyansys.com/version/stable/api/ansys/geometry/core/modeler/Modeler.html)
documentation.

## Instantiate design and initialize object list

Instantiate a new design to work on and initialize a list
of objects for plotting.

In [3]:
# init modeler
design = modeler.create_design("Multiplot")

plot_list = []

You are now ready to create some objects and use the
plotter capabilities.

## Create a PyAnsys Geometry body cylinder

Use PyAnsys Geometry to create a body cylinder.

In [4]:
cylinder = Sketch()
cylinder.circle(Point2D([10, 10], UNITS.m), 1.0)
cylinder_body = design.extrude_sketch("JustACyl", cylinder, Quantity(10, UNITS.m))
plot_list.append(cylinder_body)

## Create a PyAnsys Geometry arc sketch

Use PyAnsys Geometry to create an arc sketch.

In [5]:
sketch = Sketch()
sketch.arc(
    Point2D([20, 20], UNITS.m),
    Point2D([20, -20], UNITS.m),
    Point2D([10, 0], UNITS.m),
    tag="Arc",
)
plot_list.append(sketch)

## Create a PyVista cylinder

Use PyVista to create a cylinder.

In [6]:
cyl = pv.Cylinder(radius=5, height=20, center=(-20, 10, 10))
plot_list.append(cyl)

## Create a PyVista multiblock

Use PyVista to create a multiblock with a sphere and a cube.

In [7]:
blocks = pv.MultiBlock(
    [pv.Sphere(center=(20, 10, -10), radius=10), pv.Cube(x_length=10, y_length=10, z_length=10)]
)
plot_list.append(blocks)

## Create a PyAnsys Geometry body box

Use PyAnsys Geometry to create a body box that is a cube.

In [8]:
box2 = Sketch()
box2.box(Point2D([-10, 20], UNITS.m), Quantity(10, UNITS.m), Quantity(10, UNITS.m))
box_body2 = design.extrude_sketch("JustABox", box2, Quantity(10, UNITS.m))
plot_list.append(box_body2)

## Plot objects

When plotting the created objects, you have several options.

You can simply plot one of the created objects.

In [9]:
plotter = GeometryPlotter()
plotter.show(box_body2)

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

You can plot the whole list of objects.

In [10]:
plotter = GeometryPlotter()
plotter.show(plot_list)

/home/runner/work/pyansys-geometry/pyansys-geometry/.venv/lib/python3.13/site-packages/ansys/geometry/core/sketch/arc.py:180: PyVistaDeprecationWarning: 
../../../../.venv/lib/python3.13/site-packages/ansys/geometry/core/sketch/arc.py:180: Arguments 'pointa', 'pointb', 'center' must be passed as keyword arguments to function 'CircularArc'.
From version 0.50, passing these as positional arguments will result in a TypeError.
  return pv.CircularArc(


EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

The Python visualizer is used by default. However, you can also use
[trame](https://kitware.github.io/trame/index.html) for visualization.

```python

plotter = GeometryPlotter(use_trame=True)
plotter.show(plot_list)
```

## Clip objects

You can clip any object represented in the plotter by defining a ``Plane`` object that
intersects the target object.

In [11]:
from ansys.geometry.core.math import Plane, Point3D
pl = GeometryPlotter()

# Define PyAnsys Geometry box
box2 = Sketch()
box2.box(Point2D([-10, 20], UNITS.m), Quantity(10, UNITS.m), Quantity(10, UNITS.m))
box_body2 = design.extrude_sketch("JustABox", box2, Quantity(10, UNITS.m))

# Define plane to clip the box
origin = Point3D([-10., 20., 5.], UNITS.m)
plane = Plane(origin=origin, direction_x=[1, 1, 1], direction_y=[-1, 0, 1])

# Add the object with the clipping plane
pl.plot(box_body2, clipping_plane=plane)
pl.show()

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

## Select objects interactively

PyAnsys Geometry's plotter supports interactive object selection within the scene.
This enables you to pick objects for subsequent script manipulation.

In [12]:
plotter = GeometryPlotter(allow_picking=True)

# Plotter returns picked bodies
picked_list = plotter.show(plot_list)
print(picked_list)

/home/runner/work/pyansys-geometry/pyansys-geometry/.venv/lib/python3.13/site-packages/ansys/geometry/core/sketch/arc.py:180: PyVistaDeprecationWarning: 
../../../../.venv/lib/python3.13/site-packages/ansys/geometry/core/sketch/arc.py:180: Arguments 'pointa', 'pointb', 'center' must be passed as keyword arguments to function 'CircularArc'.
From version 0.50, passing these as positional arguments will result in a TypeError.
  return pv.CircularArc(


EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

None


It is also possible to enable picking directly for a specific ``design`` or ``component``
object alone. In the following cell, picking is enabled for the ``design`` object.

In [13]:
picked_list = design.plot(allow_picking=True)
print(picked_list)

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

None


## Render in different colors

You can render the objects in different colors automatically using PyVista's default
color cycler. In order to do this, activate the ``multi_colors=True`` option when calling
the ``plot()`` method.

In the following cell you can create a new design and plot a prism and a cylinder in different colors.

In [14]:
design = modeler.create_design("MultiColors")

# Create a sketch of a box
sketch_box = Sketch().box(Point2D([0, 0], unit=UNITS.m), width=30 * UNITS.m, height=40 * UNITS.m)

# Create a sketch of a circle (overlapping the box slightly)
sketch_circle = Sketch().circle(Point2D([20, 0], unit=UNITS.m), radius=3 * UNITS.m)

# Extrude both sketches to get a prism and a cylinder
design.extrude_sketch("Prism", sketch_box, 50 * UNITS.m)
design.extrude_sketch("Cylinder", sketch_circle, 50 * UNITS.m)

# Design plotting
design.plot(multi_colors=True)

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

## Close session

When you finish interacting with your modeling service, you should close the active
server session. This frees resources wherever the service is running.

Close the server session.

In [15]:
modeler.close()